In [2]:
from tensorflow.keras.models import load_model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, Input
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import os
import librosa
import numpy as np
import pandas as pd
import json
import joblib

In [3]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [4]:
df_scaler = joblib.load('scalers/df_scaler.pkl')
si_scaler = joblib.load('scalers/vr_scaler.pkl')
others_profile = pd.read_csv('results\\voice_recognition\\training_full\\vr_other_segment.csv')

c:\Daren\University of the East\THESIS\Thesis-Project-version1\Thesis-Project-prototype\Thesis-Project-prototype\server\venv\Lib\site-packages\sklearn\base.py:376: InconsistentVersionWarning: Trying to unpickle estimator StandardScaler from version 1.5.1 when using version 1.5.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


In [5]:
def pre_process(audio_file):
    target_sr = 22050

    signal, sr = librosa.load(audio_file, sr=target_sr, mono=False, res_type='kaiser_fast')
    if signal.ndim > 1:
        signal = np.mean(signal, axis=0)
    
    return signal, target_sr

In [6]:
def extract_MFCC(signal, sr):
    mfccs = librosa.feature.mfcc(y=signal, sr=sr, n_mfcc=13)
    
    delta_mfccs = librosa.feature.delta(mfccs)
    delta2_mfccs = librosa.feature.delta(mfccs, order=2)
    comprehensive_mfcc = np.concatenate((mfccs, delta_mfccs, delta2_mfccs))
    return comprehensive_mfcc

In [7]:
def extract_features(audio, sr, target_sr = 22050):
    FRAME_LENGTH = 1024
    HOP_LENGTH = 512

    rms_cropped = librosa.feature.rms(y=audio, frame_length=FRAME_LENGTH, hop_length=HOP_LENGTH)[0]
    zcr_cropped = librosa.feature.zero_crossing_rate(y=audio, frame_length=FRAME_LENGTH)[0]
    sc_cropped = librosa.feature.spectral_centroid(y=audio, sr=sr, n_fft=FRAME_LENGTH, hop_length=HOP_LENGTH)[0]
    sb_cropped = librosa.feature.spectral_bandwidth(y=audio, sr=sr, n_fft=FRAME_LENGTH, hop_length=HOP_LENGTH)[0]

    return rms_cropped, zcr_cropped, sc_cropped, sb_cropped

In [8]:
def process_audio_segments(audio, segment_duration = 2):
    mfcc_features = []
    rms_values = []
    zcr_values = []
    sc_values = []
    sb_values = []
    file_names = []

    for i in audio:
        segment_number = 0
        signal, sr = pre_process(i)
        segment_length = int(segment_duration*sr)
        total_length = len(signal)

        for start in range(0, total_length, segment_length):
            segment_number += 1
            end = start + segment_length
            if end > total_length:
                break

            segment = signal[start:end]

            mfcc = extract_MFCC(segment, sr)
            mfcc_mean = np.mean(mfcc.T, axis=0)
            mfcc_features.append(mfcc_mean)

            rms, zcr, sc, sb = extract_features(segment, sr)
            rms_values.append(rms)
            zcr_values.append(zcr)
            sc_values.append(sc)
            sb_values.append(sb)

            file_names.append(f"{i}_segment_{segment_number}")

    return file_names, mfcc_features, rms_values, zcr_values, sc_values, sb_values

In [ ]:
def df_segment_data(file_names, mfcc_features, rms_values, zcr_values, sc_values, sb_values):
    mfcc_df = pd.DataFrame(mfcc_features, columns=[f'MFCC{i+1}' for i in range(mfcc_features[0].shape[0])])
    rms_df = pd.DataFrame(rms_values, columns=[f'RMS{i+1}' for i in range(len(rms_values[0]))])
    zcr_df = pd.DataFrame(zcr_values, columns=[f'ZCR{i+1}' for i in range(len(zcr_values[0]))])
    sc_df = pd.DataFrame(sc_values, columns=[f'SpectralCentroid{i+1}' for i in range(len(sc_values[0]))])
    sb_df = pd.DataFrame(sb_values, columns=[f'SpectralBandwidth{i+1}' for i in range(len(sb_values[0]))])

    combined_df = pd.concat([pd.DataFrame(file_names, columns=['file_name']), mfcc_df, rms_df, zcr_df, sc_df, sb_df], axis=1)
    return combined_df

In [10]:
def reshape_segment(segment_features, scaler):
    reshaped = scaler.transform([segment_features])
    reshaped = reshaped.reshape(1, reshaped.shape[1], 1, 1)
    print(reshaped)
    return reshaped

In [11]:
def evaluate_segments(segment_data, model, scaler):
    confidence_scores = []
    for i in range(0, segment_data.shape[0]):
        segment_row = segment_data[i]
        reshaped_segment = reshape_segment(segment_row, scaler)

        predictions = model.predict(reshaped_segment)
        confidence = predictions[0][0]
        confidence = float(confidence)
        confidence_scores.append(confidence)
    
    return confidence_scores

In [12]:
def average(confidence_scores):
    return sum(confidence_scores)/len(confidence_scores)


In [13]:
files=['synthetic//spanish86_cloned.mp3', 'synthetic//swedish4_cloned.mp3', 'synthetic//tagalog12_cloned.mp3' , 'synthetic//taiwanese6_cloned.mp3' , 'synthetic//tajiki1_cloned.mp3' , 'synthetic//thai10_cloned.mp3' , 'synthetic//tigrigna5_cloned.mp3' , 'synthetic//turkish6_cloned.mp3' , 'synthetic//urdo10_cloned.mp3' , 'synthetic//yidish3_cloned.mp3' ]

In [14]:
si_segment_data = process_audio_segments(files)
speaker_profile = df_segment_data(*si_segment_data)
speaker_data = speaker_profile

In [15]:
speaker_profile['label'] = 1
others_profile['label'] = 0

In [16]:
others_profile.columns

Index(['file_name', 'mfcc_feature1', 'mfcc_feature2', 'mfcc_feature3',
       'mfcc_feature4', 'mfcc_feature5', 'mfcc_feature6', 'mfcc_feature7',
       'mfcc_feature8', 'mfcc_feature9',
       ...
       'SpectralBandwidth79', 'SpectralBandwidth80', 'SpectralBandwidth81',
       'SpectralBandwidth82', 'SpectralBandwidth83', 'SpectralBandwidth84',
       'SpectralBandwidth85', 'SpectralBandwidth86', 'SpectralBandwidth87',
       'label'],
      dtype='object', length=389)

In [17]:
speaker_profile.columns

Index(['file_name', 'mfcc_feature1', 'mfcc_feature2', 'mfcc_feature3',
       'mfcc_feature4', 'mfcc_feature5', 'mfcc_feature6', 'mfcc_feature7',
       'mfcc_feature8', 'mfcc_feature9',
       ...
       'SpectralBandwidth79', 'SpectralBandwidth80', 'SpectralBandwidth81',
       'SpectralBandwidth82', 'SpectralBandwidth83', 'SpectralBandwidth84',
       'SpectralBandwidth85', 'SpectralBandwidth86', 'SpectralBandwidth87',
       'label'],
      dtype='object', length=389)

In [18]:
data_df = pd.concat([speaker_profile, others_profile], ignore_index=True)


In [19]:
data_df

file_name  mfcc_feature1  \
0            synthetic//spanish86_cloned.mp3_segment_1    -231.127136   
1            synthetic//spanish86_cloned.mp3_segment_2    -246.181412   
2            synthetic//spanish86_cloned.mp3_segment_3    -271.776367   
3            synthetic//spanish86_cloned.mp3_segment_4    -263.963074   
4            synthetic//spanish86_cloned.mp3_segment_5    -279.814819   
5            synthetic//spanish86_cloned.mp3_segment_6    -244.786026   
6            synthetic//spanish86_cloned.mp3_segment_7    -246.811081   
7            synthetic//spanish86_cloned.mp3_segment_8    -218.102936   
8             synthetic//swedish4_cloned.mp3_segment_1    -146.949646   
9             synthetic//swedish4_cloned.mp3_segment_2    -173.697159   
10            synthetic//swedish4_cloned.mp3_segment_3    -225.157639   
11            synthetic//swedish4_cloned.mp3_segment_4    -173.753174   
12            synthetic//swedish4_cloned.mp3_segment_5    -164.328018   
13            synthetic//swedish4_cloned.mp3_segment_6    -127.168442   
14            synthetic//swedish4_cloned.mp3_segment_7    -134.739487   
15           synthetic//tagalog12_cloned.mp3_segment_1    -219.023972   
16           synthetic//tagalog12_cloned.mp3_segment_2    -210.083588   
17           synthetic//tagalog12_cloned.mp3_segment_3    -250.930496   
18           synthetic//tagalog12_cloned.mp3_segment_4    -295.402893   
19           synthetic//tagalog12_cloned.mp3_segment_5    -171.430389   
20           synthetic//tagalog12_cloned.mp3_segment_6    -193.361313   
21          synthetic//taiwanese6_cloned.mp3_segment_1    -196.742844   
22          synthetic//taiwanese6_cloned.mp3_segment_2    -218.081940   
23          synthetic//taiwanese6_cloned.mp3_segment_3    -279.000458   
24          synthetic//taiwanese6_cloned.mp3_segment_4    -234.886658   
25          synthetic//taiwanese6_cloned.mp3_segment_5    -248.484573   
26             synthetic//tajiki1_cloned.mp3_segment_1    -167.343719   
27             synthetic//tajiki1_cloned.mp3_segment_2    -184.919281   
28             synthetic//tajiki1_cloned.mp3_segment_3    -177.005493   
29             synthetic//tajiki1_cloned.mp3_segment_4    -142.873764   
30              synthetic//thai10_cloned.mp3_segment_1    -161.354294   
31              synthetic//thai10_cloned.mp3_segment_2    -187.012299   
32              synthetic//thai10_cloned.mp3_segment_3    -225.807404   
33              synthetic//thai10_cloned.mp3_segment_4    -185.911285   
34              synthetic//thai10_cloned.mp3_segment_5    -221.823013   
35           synthetic//tigrigna5_cloned.mp3_segment_1    -200.451416   
36           synthetic//tigrigna5_cloned.mp3_segment_2    -241.465469   
37           synthetic//tigrigna5_cloned.mp3_segment_3    -247.812943   
38           synthetic//tigrigna5_cloned.mp3_segment_4    -224.649216   
39           synthetic//tigrigna5_cloned.mp3_segment_5    -260.282196   
40           synthetic//tigrigna5_cloned.mp3_segment_6    -295.328339   
41           synthetic//tigrigna5_cloned.mp3_segment_7    -264.128601   
42           synthetic//tigrigna5_cloned.mp3_segment_8    -228.222382   
43            synthetic//turkish6_cloned.mp3_segment_1    -239.439850   
44            synthetic//turkish6_cloned.mp3_segment_2    -275.849915   
45            synthetic//turkish6_cloned.mp3_segment_3    -295.145233   
46            synthetic//turkish6_cloned.mp3_segment_4    -239.139008   
47            synthetic//turkish6_cloned.mp3_segment_5    -231.729706   
48            synthetic//turkish6_cloned.mp3_segment_6    -252.326279   
49            synthetic//turkish6_cloned.mp3_segment_7    -255.865234   
50            synthetic//turkish6_cloned.mp3_segment_8    -305.603058   
51            synthetic//turkish6_cloned.mp3_segment_9    -206.752289   
52           synthetic//turkish6_cloned.mp3_segment_10    -264.105011   
53              synthetic//urdo10_cloned.mp3_segment_1    -197.561264   
54              synthetic//urd

In [20]:
data_df = data_df.sample(frac=1).reset_index(drop=True)


In [21]:
X = data_df.drop(columns=['file_name','label']).values
y = data_df['label'].values

In [22]:
X.shape[1]

387

In [62]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)
X_train = X_train.reshape((X_train.shape[0], X_train.shape[1], 1, 1))
X_test = X_test.reshape((X_test.shape[0], X_test.shape[1], 1, 1))
input_shape = (X_train.shape[1], 1, 1)

In [64]:
speaker_identification_model = Sequential([
    Conv2D(16, (3, 3), activation='relu', input_shape=input_shape, padding='same'),
    MaxPooling2D((2,1)),

    Conv2D(32, (3, 3), activation='relu', padding='same'),
    MaxPooling2D((2,1)),

    Flatten(),
    Dense(64, activation='relu'),
    Dropout(0.5),

    Dense(1, activation='sigmoid')
])

In [65]:
speaker_identification_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
speaker_identification_model.fit(X_train, y_train, epochs=20, batch_size=16, validation_split=0.2)
speaker_identification_model.evaluate(X_test, y_test)
si_model = speaker_identification_model

Epoch 1/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 5s 141ms/step - accuracy: 0.5244 - loss: 0.6844 - val_accuracy: 0.7778 - val_loss: 0.5753
Epoch 2/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6368 - loss: 0.6399 - val_accuracy: 0.7778 - val_loss: 0.5455
Epoch 3/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.7393 - loss: 0.5986 - val_accuracy: 0.7778 - val_loss: 0.4993
Epoch 4/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.7994 - loss: 0.5023 - val_accuracy: 0.8333 - val_loss: 0.4905
Epoch 5/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - accuracy: 0.8973 - loss: 0.4379 - val_accuracy: 0.8889 - val_loss: 0.5018
Epoch 6/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - accuracy: 0.8079 - loss: 0.4374 - val_accuracy: 0.8333 - val_loss: 0.3843
Epoch 7/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - accuracy: 0.8826 - loss: 0.3514 - val_accuracy: 0.8333 - val_loss: 0.3701
Epoch 8/20
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - accuracy: 0.9232 - loss: 0.3093 - val_accuracy: 0.8333 - val_loss: 0.3683

In [ ]:
test = ['spanish86_cloned.mp3']
testing = process_audio_segments(test)
si_segment_data_df = df_segment_data(*testing)
si_segment_data_values = si_segment_data_df.drop(columns=['file_name']).values

[[[[ 1.28969162e+00]]

  [[ 2.10545489e+00]]

  [[ 7.85998466e-01]]

  [[-1.49275024e+00]]

  [[-1.03245480e+00]]

  [[-2.46395480e-01]]

  [[ 2.61038370e-02]]

  [[-1.85352941e+00]]

  [[-1.89302638e+00]]

  [[-1.26013149e+00]]

  [[ 1.67117012e-01]]

  [[-5.12959460e-01]]

  [[-4.96298798e-01]]

  [[ 1.80015732e+00]]

  [[ 2.59572018e+00]]

  [[-5.18518280e-02]]

  [[-1.57532934e+00]]

  [[-2.57261963e-02]]

  [[ 6.87983572e-01]]

  [[-1.80879395e+00]]

  [[-3.82532636e+00]]

  [[-3.28143621e+00]]

  [[-6.46136992e-01]]

  [[-4.47341715e-01]]

  [[-9.21174317e-01]]

  [[-2.37958322e-01]]

  [[ 2.90355491e-01]]

  [[-6.08583083e-01]]

  [[-8.00597761e-01]]

  [[ 9.18704726e-01]]

  [[-9.26975740e-01]]

  [[-9.13175959e-01]]

  [[ 2.03079763e-01]]

  [[ 8.73207125e-01]]

  [[-5.67812584e-01]]

  [[ 8.83895961e-01]]

  [[ 4.75883026e-01]]

  [[-9.15534568e-01]]

  [[-1.04890922e+00]]

  [[-8.17216340e-01]]

  [[-8.27847960e-01]]

  [[-8.07370744e-01]]

  [[-8.07838956e-01]]

  [[-7.7216

In [68]:
si_segment_data_values

array([[-2.31127136e+02,  1.66375809e+02, -3.59979224e+00, ...,
         6.92035675e+02,  7.97223058e+02,  2.02487054e+03],
       [-2.46181412e+02,  1.25979584e+02, -1.30601263e+01, ...,
         9.45513280e+02,  1.05219650e+03,  1.66497376e+03],
       [-2.71776367e+02,  1.68092285e+02, -1.22027655e+01, ...,
         8.00196929e+02,  6.14939932e+02,  2.43344556e+03],
       ...,
       [-2.44786026e+02,  1.22178383e+02, -1.12210569e+01, ...,
         2.05842529e+03,  2.30743286e+03,  2.34614084e+03],
       [-2.46811081e+02,  1.42358780e+02, -2.06512761e+00, ...,
         2.17984458e+03,  9.10348493e+02,  2.59670097e+03],
       [-2.18102936e+02,  1.17703728e+02, -1.54396706e+01, ...,
         1.91822919e+03,  1.74064044e+03,  1.83953723e+03]])

In [72]:
evaluate = evaluate_segments(si_segment_data_values, si_model, si_scaler)
overall = average(evaluate)

[[[[ 1.28969162e+00]]

  [[ 2.10545489e+00]]

  [[ 7.85998466e-01]]

  [[-1.49275024e+00]]

  [[-1.03245480e+00]]

  [[-2.46395480e-01]]

  [[ 2.61038370e-02]]

  [[-1.85352941e+00]]

  [[-1.89302638e+00]]

  [[-1.26013149e+00]]

  [[ 1.67117012e-01]]

  [[-5.12959460e-01]]

  [[-4.96298798e-01]]

  [[ 1.80015732e+00]]

  [[ 2.59572018e+00]]

  [[-5.18518280e-02]]

  [[-1.57532934e+00]]

  [[-2.57261963e-02]]

  [[ 6.87983572e-01]]

  [[-1.80879395e+00]]

  [[-3.82532636e+00]]

  [[-3.28143621e+00]]

  [[-6.46136992e-01]]

  [[-4.47341715e-01]]

  [[-9.21174317e-01]]

  [[-2.37958322e-01]]

  [[ 2.90355491e-01]]

  [[-6.08583083e-01]]

  [[-8.00597761e-01]]

  [[ 9.18704726e-01]]

  [[-9.26975740e-01]]

  [[-9.13175959e-01]]

  [[ 2.03079763e-01]]

  [[ 8.73207125e-01]]

  [[-5.67812584e-01]]

  [[ 8.83895961e-01]]

  [[ 4.75883026e-01]]

  [[-9.15534568e-01]]

  [[-1.04890922e+00]]

  [[-8.17216340e-01]]

  [[-8.27847960e-01]]

  [[-8.07370744e-01]]

  [[-8.07838956e-01]]

  [[-7.7216

In [76]:
speaker_data = speaker_profile[sorted(
    [col for col in speaker_profile.columns],
    key=lambda x: int(x[3:])
)]

ValueError: invalid literal for int() with base 10: 'e_name'

In [26]:
speaker_profile.to_dict(orient="records")

[{'file_name': 'synthetic//spanish86_cloned.mp3_segment_1',
  'mfcc_feature1': -231.12713623046875,
  'mfcc_feature2': 166.3758087158203,
  'mfcc_feature3': -3.599792242050171,
  'mfcc_feature4': 15.212297439575195,
  'mfcc_feature5': -20.045907974243164,
  'mfcc_feature6': 1.8965808153152466,
  'mfcc_feature7': -9.695122718811035,
  'mfcc_feature8': -17.47812271118164,
  'mfcc_feature9': -24.64613151550293,
  'mfcc_feature10': -10.667757034301758,
  'mfcc_feature11': -7.389188289642334,
  'mfcc_feature12': -8.601448059082031,
  'mfcc_feature13': -3.3272182941436768,
  'mfcc_feature14': 3.359271764755249,
  'mfcc_feature15': 2.5158867835998535,
  'mfcc_feature16': -0.07106171548366547,
  'mfcc_feature17': -0.7582055330276489,
  'mfcc_feature18': -0.02691654860973358,
  'mfcc_feature19': 0.2916814982891083,
  'mfcc_feature20': -0.46339502930641174,
  'mfcc_feature21': -0.7713696956634521,
  'mfcc_feature22': -0.584217369556427,
  'mfcc_feature23': -0.1144070103764534,
  'mfcc_feature24'

In [29]:
response_data = {
    "order" : 1,
    "uploaded_data": speaker_profile.to_dict(orient="records")
}

In [30]:
response_data

{'order': 1,
 'uploaded_data': [{'file_name': 'synthetic//spanish86_cloned.mp3_segment_1',
   'mfcc_feature1': -231.12713623046875,
   'mfcc_feature2': 166.3758087158203,
   'mfcc_feature3': -3.599792242050171,
   'mfcc_feature4': 15.212297439575195,
   'mfcc_feature5': -20.045907974243164,
   'mfcc_feature6': 1.8965808153152466,
   'mfcc_feature7': -9.695122718811035,
   'mfcc_feature8': -17.47812271118164,
   'mfcc_feature9': -24.64613151550293,
   'mfcc_feature10': -10.667757034301758,
   'mfcc_feature11': -7.389188289642334,
   'mfcc_feature12': -8.601448059082031,
   'mfcc_feature13': -3.3272182941436768,
   'mfcc_feature14': 3.359271764755249,
   'mfcc_feature15': 2.5158867835998535,
   'mfcc_feature16': -0.07106171548366547,
   'mfcc_feature17': -0.7582055330276489,
   'mfcc_feature18': -0.02691654860973358,
   'mfcc_feature19': 0.2916814982891083,
   'mfcc_feature20': -0.46339502930641174,
   'mfcc_feature21': -0.7713696956634521,
   'mfcc_feature22': -0.584217369556427,
   'mf